In [36]:
import gzip
import math
import statistics as stats
import random
from collections import defaultdict
import numpy as np
import pandas as pd
from sklearn import linear_model
import json
import regex as re

In [2]:
#def parse(path):
#    g = gzip.open(path, 'r', encoding = 'utf-8')
#    for l in g:
#        yield json.loads(l)
#data = list(parseData("Video_Games.json.gz"))

In [3]:
#def parseData(fname):
#    for l in open(fname):
#        yield eval(l)
#        
#data = list(parseData("Video_Games.json"))

In [4]:
#import json
#with open('Video_Games.json') as f:
#   data = json.load(f)

In [5]:
df = pd.read_json('Video_Games.json.gz', lines=True)

In [6]:
df[:5]

overall  verified   reviewTime      reviewerID        asin  \
0        1      True   06 9, 2014  A21ROB4YDOZA5P  0439381673   
1        3      True  05 10, 2014  A3TNZ2Q5E7HTHD  0439381673   
2        4      True   02 7, 2014  A1OKRM3QFEATQO  0439381673   
3        1      True   02 7, 2014  A2XO1JFCNEYV3T  0439381673   
4        4      True  01 16, 2014  A19WLPIRHD15TH  0439381673   

       reviewerName                                         reviewText  \
0     Mary M. Clark  I used to play this game years ago and loved i...   
1         Sarabatya  The game itself worked great but the story lin...   
2   Amazon Customer  I had to learn the hard way after ordering thi...   
3  ColoradoPartyof5  The product description should state this clea...   
4    Karen Robinson  I would recommend this learning game for anyon...   

                                             summary  unixReviewTime vote  \
0                                  Did not like this      1402272000  NaN   
1                                     Almost Perfect      1399680000  NaN   
2  DOES NOT WORK WITH MAC OS unless it is 10.3 or...      1391731200   15   
3                           does not work on Mac OSX      1391731200   11   
4                                        Roughing it      1389830400  NaN   

  style image  
0   NaN   NaN  
1   NaN   NaN  
2   NaN   NaN  
3   NaN   NaN  
4   NaN   NaN

## 1. EDA

In [8]:
data = df.sample(n = 100000)
data[:5]

overall  verified   reviewTime      reviewerID        asin  \
783702         5      True  09 26, 2015   APNT1D2QYK6RK  B003CP0BHM   
841292         1      True  06 27, 2016  A3D4H77M145XTC  B0042J7I3C   
739543         2      True  11 19, 2012  A2OOYT66R1S2TW  B002D2Y3IS   
2176259        4     False  06 13, 2001  A3MZVAG3ATUD7H  B00002STHI   
1214339        5     False  04 15, 2015  A1BYPIGZJJ0CHZ  B00BGA9WK2   

        reviewerName                                         reviewText  \
783702     JoKollene  So the adjustability is fantastic. Still SLIGH...   
841292         Deana                                  Broke in two days   
739543        German  I bought 4 controls, 2 have the nunchung damag...   
2176259        Jesse  Needs more cars!!  They should have made this ...   
1214339       Kiburi                                           Love it.   

                   summary  unixReviewTime vote  \
783702   I have tiny hands      1443225600  NaN   
841292            One Star      1466985600  NaN   
739543     damage nunchunk      1353283200  NaN   
2176259              ok...       992390400    5   
1214339         Five Stars      1429056000  NaN   

                                               style image  
783702   {'Color:': ' Black', 'Style:': ' R.A.T. 7'}   NaN  
841292                          {'Color:': ' White'}   NaN  
739543                                           NaN   NaN  
2176259                                          NaN   NaN  
1214339                                          NaN   NaN

**------------This needs to be cited-------------** <br>
Jianmo Ni, Jiacheng Li, Julian McAuley
Empirical Methods in Natural Language Processing (EMNLP), 2019

The dataset we have chosen to work with are video game reviews on Amazon from 2014. There are 2,565,349 reviews in total, however for the purpose of computation, we have sampled 100,000 reviews. The data consists of 12 features: overall rating, verified (binary), time of review (raw), reviewer ID, product ID, name of reviewer, text of review, summary of product, time of review (unix), helpfulness votes (likes), product style, and attached image. 

Lets take a look at the data type for each column, and how many non-null values there are. 

In [10]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 100000 entries, 783702 to 1070226
Data columns (total 12 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   overall         100000 non-null  int64 
 1   verified        100000 non-null  bool  
 2   reviewTime      100000 non-null  object
 3   reviewerID      100000 non-null  object
 4   asin            100000 non-null  object
 5   reviewerName    99987 non-null   object
 6   reviewText      99936 non-null   object
 7   summary         99967 non-null   object
 8   unixReviewTime  100000 non-null  int64 
 9   vote            17173 non-null   object
 10  style           51599 non-null   object
 11  image           1127 non-null    object
dtypes: bool(1), int64(2), object(9)
memory usage: 9.3+ MB


Lets add some features, like length of review text and length of summary, and replace NAN values with 0 for votes to perform some basic statistics.

In [23]:
data = data[['overall', 'reviewTime', 'reviewText', 'summary', 'unixReviewTime', 'vote']]

data['vote'] = data['vote'].replace(np.nan, 0).astype(float)
data['reviewText'] = data['reviewText'].replace(np.nan, '')
data['summary'] = data['summary'].replace(np.nan, '')

data['len_reviewText'] = [len(x) for x in data['reviewText']]
data['len_summary'] = [len(x) for x in data['summary']]

In [24]:
data[['overall', 'vote', 'len_reviewText', 'len_summary']].describe()

overall           vote  len_reviewText    len_summary
count  100000.000000  100000.000000   100000.000000  100000.000000
mean        4.029030       1.424350      401.066210      23.509600
std         1.401009      10.215607      804.474242      18.955359
min         1.000000       0.000000        0.000000       0.000000
25%         3.000000       0.000000       54.000000      10.000000
50%         5.000000       0.000000      151.000000      16.000000
75%         5.000000       0.000000      400.000000      32.000000
max         5.000000     989.000000    23832.000000     283.000000

In [ ]:
#Histogram on months, extract months for each review and bar plot count per months**
#Bivariative: 

## 2. Predictive Task (Baseline)

In [33]:
data[['reviewText']][]

reviewText
783702   So the adjustability is fantastic. Still SLIGH...
841292                                   Broke in two days
739543   I bought 4 controls, 2 have the nunchung damag...
2176259  Needs more cars!!  They should have made this ...
1214339                                           Love it.
...                                                    ...
1003408  I finally gave up on wireless mice and searche...
1100941  Had trouble downloading and wanted a refund.  ...
1820124            Very good product and smells very good!
856567   I am so mad because it doesn't work and I have...
1070226                                          pipi cucu

[100000 rows x 1 columns]

In [34]:
for d in data['reviewText']:
    print(re.sub(r'[^\w\s]',' ', d.lower()))

So the adjustability is fantastic. Still SLIGHTLY too big for my hand but I am very pleased with it.
Most definitely recommend.
Broke in two days
I bought 4 controls, 2 have the nunchung damage, the jostick not back to center. sometimes  don't is exact the position from  pointer in the display.
Needs more cars!!  They should have made this game with more cars!!  You should be able to start with all of the cars and then as you go on you get them upgraded:different levels of greatness!!  Controling the cars is kinda hard to do tooo...
Love it.
Retailers quit selling this item locally because of people opening them up before purchasing it and it posed a health hazzard, so... I gave one to my girlfriend and she loves it also. Perfect item
But this game because of the 3D ride at Disneyland did not disappoint Its what I would expect with Disney/Pixar I would like to commend this seller my game came before other items I ordered weeks before they accurately gave the best description of there i

So cute! I was lucky to get a good price too. I love San-x!
The game work fine no problem and received on time and will order from this seller again.
My grandson was disappointed that the game didn't follow the movie very well and he said it's easy to get "off track" when playing.  He's 12 and very savvy playing video games.
Broke after a few weeks. Could not control character.
Have been looking forward to this game for 20 years but after reading all the reviews, I've decided to skip Diablo 3. Mainly because of the online only thing. This is why I never buy games the day they come out. I just saved 60 bucks.
Awesome game.
This little bag here is perfect for transporting the PS4 system. It holds the system, pocket for cables, 2 game cases, ps4 camera and 2 controllers. It's not bulky either.
It does what its suppose to! and its doesn't slip around where i have it hidden from my children.
Kids like it. Use it a lot. Good product I have nothing to add but the system is asking me for a min

Perfect dust cover. Just what I was looking for!
it's fine
I bought this game at noon. I went home and within two hours I beat the game twice. This game has no challenge what so ever. I never even read the directions. This game may be good for younger kids but older player will walk right through this game. I sold it to Funcoland two hours after i bought it because there was just no challenge to the game. very disapointing for any huge wrestling fan.
PS4 finger grip, they look great and feel great. the only problem is they are a little too thick and effects some game play.
 ..Like for an example, when i play ww2 you have to press down on L3 to run and sometime it doesn't run because of the thickness of the finger grip.
Enslaved is the first game I bought with my PS3 in November 2010. honestly I really love the idea of controlling more than one character at once - kind of like Kingdom Hearts. not only that, but the graphics ended up amazing, and the voiceovers were as well. (It was nice

easy to pick up and play and for a golf game 4 years old suprisingly playable and good lucking in the graphics :)
Awesome series.
Best versions of Civ ever made.
Good
good
This game is great, a little old compared to the new total war games but its awesome. My only qualm is that you cant fight sea battles and if you allow the computer to simulate your battles your army might get jacked up.
Only con I have for this headset is that you have to press the mute button the whole time to stay mute. Other then that great sound and mic is awesome.
What a great buy this was.  We are going to save a lot of money on batteries.  I like that it is not connected to the Wii unit and we can put it where ever we want.  No problems at all.
I got this for Christmas and I was been playing it for 5 months and this game was terrible! It has bad graphics and the game producers wants u to die on the last part! Get black ops it is way better than this stupid game! I don't get it how people thinks it's way bette

Four cute, perfect little stylus packaged individually.  The price is amazing!!  I think I purchased too many which is a good thing because now I have back ups.
This was a fitting end to the trilogy, bringing back most of your favorite companions and even random acquaintances from throughout the series. There are some touching farewells and shared memories. Additionally, the Citadel DLC really drove home the depth of the journey taken with your companions over all these years.

The multiplayer mode ended up being a surprising bonus, bringing in friends who normally never play multiplayer games, since it provided a pretty familiar interface set in the Mass Effect universe with an in-game incentive to participate. Cooperative play really was the best way to further the Mass Effect experience. Even now, my friends will occasionally get the hankering to pull out Mass Effect 3 for a few more rounds of multiplayer.
just like the ones from my NN3DSXL! :D very happy with these
Worth the playth

...

I have had this headset for over 3 years now and do not regret my purchase. The mic has never failed me, and the audio quality on these things (though not Audiophile level), but better than most other headphones and earbuds at this price level. Pair these guys up with a 3.5 MM Jack to USB and you have got yourself a killer audio setup for your PC command station!
Fix the dang connection and hit registration issues!!!! I have done everything I could to try and fix the connection issues. It keeps telling me that there is "probably" a strict NAT problem with an error code that apparently means nothing. This is the only multiplayer game I have with this issue. Worst part is that it's intermediate. Hit registration is awful. A lot of the time I don't know people are shooting at me until I'm dead. I watch the kill cam and the dude unloaded a magazine before he finally got a lucky shot on me. Sometimes I kill people in three shots and other times I have half a magazine in the person. This gam

Still works great after a year - Zero issues, took very little time to develop muscle memory.
old school
I bought this as a present for a friend. I have been playing all four campaigns for nearly two years now and still find it engrossing. One of the BEST features is that you do NOT pay a monthly fee, (sometimes as much as $50) to play a game you OWN.
This game is an incredibly scaled down version of the battlefield games. It is beyond basic. The only thing you do is run around and shoot, there's not really any other reaction. Flying is a joke because there's no way to escape a semi competent enemy that is tracking you. The vehicles and power ups are horrible because they are randomly scattered throughout the map. There are only 4 maps and a handful of weapons. All the weapons are WW2 firearms with additions on them in attempt to cover that up. There's really only one game mode too. In about 3 hours you're tired of the game because it's just so repetitive. Sometimes you won't even make

So, if you have an issue with your ears being squished after wearing headphones for a long time: Don't buy this. I used to have Sony MDR-XB500 and those have HUUUGE cushions and are super deep. I wanted headphones with a mic, but I am still disappointed by these.
I had the Logitech MX518 for years and I loved that thing the only reason I decided to replace it was because it was starting to get worn out.  I decided to go with the G9X because I really liked Logitech's mice.  The only problem I had with this one was the middle mouse wheel.  Some reviewers complain that it was to hard to press.  I'm beginning to think that my mouse may be flawed because it is overly sensitive and way to easy for me to accidentally press.  I have even had to resort to unbinding the key in a few games.  Its not a huge issue for me but it does get a bit annoying when it happens.  Other than that I still really enjoy this mouse the sensitivity settings are great and easy.
its ok
It's a clip. It does the job. W

I WAS STILL BEING TOLD TO RECHARGE ARE CHARGING IT OVER NIGHT.
Great
Great Game
nice
This product was exactly what my son wanted. He says it works great!
kids love it!
it has digital optical out for sound. I need component audio.
I have 1 year been with my psp, I have tried almost everything the headsets, 3 type of protectors from the Logitech, Sony official and at last but not less the Stealth one. I ended up selling the other 2 as this Stealth one has captured my attention.

The case is really worth what I paid, I bought it on Ebay, its pure Aluminum (aside from other cases that are plastic made), it has a protective cover inside that won't let your PSP touch the metallic externals. This is great as the external is really hard, if you are in a cold enviorment the Case will be cool as well. You can notice this is not plastic, its metal as you put your fingers or you are in the cold weather.

I agree with previous reviewers the case is heavy, but is totally worth it, I cant leave my PS

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [38]:
for d in data['reviewText']:
    print(re.sub(r'[^\w\s]',' ', d.lower()).split())

['so', 'the', 'adjustability', 'is', 'fantastic', 'still', 'slightly', 'too', 'big', 'for', 'my', 'hand', 'but', 'i', 'am', 'very', 'pleased', 'with', 'it', 'most', 'definitely', 'recommend']
['broke', 'in', 'two', 'days']
['i', 'bought', '4', 'controls', '2', 'have', 'the', 'nunchung', 'damage', 'the', 'jostick', 'not', 'back', 'to', 'center', 'sometimes', 'don', 't', 'is', 'exact', 'the', 'position', 'from', 'pointer', 'in', 'the', 'display']
['needs', 'more', 'cars', 'they', 'should', 'have', 'made', 'this', 'game', 'with', 'more', 'cars', 'you', 'should', 'be', 'able', 'to', 'start', 'with', 'all', 'of', 'the', 'cars', 'and', 'then', 'as', 'you', 'go', 'on', 'you', 'get', 'them', 'upgraded', 'different', 'levels', 'of', 'greatness', 'controling', 'the', 'cars', 'is', 'kinda', 'hard', 'to', 'do', 'tooo']
['love', 'it']
['retailers', 'quit', 'selling', 'this', 'item', 'locally', 'because', 'of', 'people', 'opening', 'them', 'up', 'before', 'purchasing', 'it', 'and', 'it', 'posed', 'a

['this', 'game', 'is', 'like', 'a', 'virgin', 'the', 'first', 'time', 'you', 'play', 'it', 'its', 'short', 'and', 'not', 'very', 'good', 'but', 'the', 'more', 'you', 'play', 'it', 'the', 'better', 'it', 'gets', 'as', 'you', 'play', 'each', 'level', 'over', 'you', 'get', 'higher', 'difficulties', 'more', 'targets', 'different', 'paths', 'to', 'choose', 'more', 'difficult', 'bosses', 'to', 'defeat', 'also', 'as', 'you', 'play', 'you', 'get', 'higher', 'ranks', 'and', 'with', 'ranks', 'come', 'unlocked', 'weapons', 'and', 'outfits', 'its', 'a', 'great', 'game', 'if', 'you', 'have', '15', 'minutes', 'you', 'want', 'to', 'kill']
['i', 'found', 'my', 'old', 'ps2', 'and', 'became', 'nostalgic', 'bought', 'these', 'games', 'and', 'haven', 't', 'stopped', 'playing', 'since', 'the', 'discs', 'are', 'functionally', 'which', 'was', 'a', 'concern', 'of', 'mine', 'they', 're', 'in', 'great', 'condition']
['perfect', 'for', 'making', 'sure', 'that', 'those', 'pesky', 'inbound', 'skype', 'calls', 'nev

['my', 'kids', 'loves', 'it']
['it', 's', 'gta', '3', 'what', 'more', 'do', 'i', 'need', 'to', 'say', 'haven', 't', 'played', 'too', 'much', 'for', 'actual', 'plot', 'but', 'the', 'game', 'is', 'still', 'a', 'classic', 'plus', 'the', 'graphics', 'are', 'better', 'than', 'the', 'ps2', 'version', 'as', 'well', 'as', 'the', 'computer', 'version']
['awesome']
['the', 'camera', 'cover', 'fits', 'securely', 'and', 'is', 'easy', 'to', 'remove', 'this', 'stand', 'also', 'provides', 'more', 'mounting', 'options', 'and', 'versatility', 'than', 'the', 'one', 'included', 'in', 'the', 'xbox', 'one']
['this', 'is', 'a', 'great', 'product', 'i', 'was', 'fortunate', 'enough', 'to', 'receive', 'the', 'correct', 'set', 'but', 'even', 'if', 'i', 'hadn', 't', 'i', 'wouldn', 't', 'rate', 'the', 'product', 'poorly', 'because', 'of', 'a', 'shipping', 'error', 'anyway', 'the', 'sound', 'quality', 'is', 'very', 'good', 'not', 'fantastic', 'but', 'what', 'can', 'you', 'expect', 'you', 're', 'spending', 'a', 'me

['i', 'originally', 'bought', 'the', 'game', 'for', 'the', 'halo', '3', 'beta', 'and', 'didn', 't', 'really', 'look', 'into', 'playing', 'crackdown', 'much', 'a', 'friend', 'on', 'xbox', 'live', 'told', 'me', 'to', 'try', 'it', 'out', 'and', 'to', 'my', 'suprise', 'the', 'game', 'was', 'actually', 'good', 'it', 'is', 'quite', 'easy', 'to', 'reach', 'the', 'maximum', 'skill', 'level', 'but', 'it', 'takes', 'time', 'i', 'really', 'ejoyed', 'being', 'able', 'to', 'jump', 'building', 'to', 'building', 'and', 'lifting', 'huge', 'objects', 'the', 'one', 'thing', 'that', 'could', 'have', 'made', 'the', 'game', 'better', 'would', 'be', 'more', 'vehicles', 'yes', 'i', 'know', 'you', 'can', 'buy', 'some', 'online', 'but', 'what', 'a', 'waste', 'of', 'money', 'they', 'could', 'have', 'included', 'a', 'helicopter', 'or', 'a', 'motor', 'cycle', 'in', 'the', 'original', 'game', 'if', 'you', 'ask', 'me', 'is', 'the', 'game', 'worth', '60', 'bucks', 'i', 'will', 'say', 'no', 'but', '30', 'to', '40', '

['the', 'company', 'sent', 'me', 'a', 'game', 'for', 'xbox', '360', 'but', 'was', 'supposed', 'to', 'be', 'for', 'the', 'wii', 'i', 'ended', 'up', 'selling', 'it']
['you', 'have', 'to', 'set', 'the', 'batteries', 'just', 'right', 'for', 'a', 'good', 'charge']
['i', 've', 'given', 'this', 'game', 'another', 'chance', 'my', 'original', 'review', 'was', 'a', 'bit', 'harsh', 'after', 'spending', 'more', 'time', 'playing', 'the', 'game', 'and', 'getting', 'used', 'to', 'the', 'way', 'the', 'new', 'game', 'flows', 'as', 'compared', 'to', '2000', 'i', 've', 'got', 'a', 'slightly', 'different', 'review', 'while', 'the', 'game', 'is', 'definetly', 'prettier', 'to', 'look', 'at', 'the', 'boxers', 'and', 'the', 'graphics', 'lack', 'fluid', 'realism', 'and', 'motion', 'which', '2000', 'had', 'it', 's', 'difficult', 'to', 'defend', 'with', 'the', 'robotic', 'movements', 'the', 'boxers', 'move', 'slow', 'i', 'find', 'it', 'annoying', 'that', 'you', 'can', 'hammer', 'your', 'opponent', 'with', 'regul

['i', 'did', 'my', 'research', 'on', 'amazon', 'to', 'find', 'the', 'optimal', 'stand', 'for', 'my', 'ps4', 'slim', 'this', 'brand', 'was', 'what', 'i', 'ultimately', 'decided', 'on', 'because', 'of', 'its', 'shape', 'reviews', 'and', 'lack', 'of', 'annoying', 'blue', 'light', 'here', 's', 'my', 'assessment', 'of', 'the', 'important', 'stuff', 'the', 'usb', 'ports', 'work', 'just', 'fine', 'i', 'had', 'no', 'problems', 'the', 'stand', 'itself', 'is', 'sturdy', 'and', 'holds', 'the', 'ps4', 'slim', 'in', 'place', 'without', 'too', 'much', 'problem', 'although', 'i', 'have', 'no', 'other', 'stand', 'to', 'compare', 'it', 'to', 'it', 's', 'a', 'tight', 'fit', 'and', 'it', 'seems', 'deep', 'enough', 'to', 'make', 'me', 'feel', 'pretty', 'secure', 'about', 'it', 'so', 'its', 'fine', 'the', 'fans', 'are', 'a', 'lot', 'noisier', 'than', 'i', 'expected', 'so', 'i', 'subtracted', 'a', 'star', 'but', 'since', 'i', 'don', 't', 'have', 'any', 'other', 'stand', 'to', 'compare', 'it', 'too', 'you', 

['my', 'original', 'reasons', 'for', 'buying', 'a', 'game', 'console', 'was', 'to', 'have', 'brain', 'age', 'the', 'sales', 'man', 'convinced', 'me', 'while', 'being', '32', 'to', 'get', 'a', 'psp', 'instead', 'of', 'a', 'nintendo', 'but', 'i', 'mentioned', 'wanting', 'to', 'have', 'a', 'brain', 'game', 'i', 'was', 'suggested', 'hot', 'brain', 'it', 'turned', 'out', 'good', 'it', 'is', 'a', 'fun', 'game', 'challenging', 'and', 'one', 'game', 'that', 'you', 'can', 'play', 'over', 'and', 'over', 'again', 'no', 'problem', 'it', 'is', 'much', 'more', 'graphic', 'then', 'the', 'original', 'brain', 'age', 'from', 'nintendo', 'it', 'gives', 'you', 'challenges', 'in', '5', 'different', 'catagories', 'and', 'the', 'assignments', 'are', 'very', 'nice', 'and', 'random', 'if', 'you', 'are', 'looking', 'for', 'the', 'best', 'brain', 'age', 'comparison', 'i', 'think', 'mind', 'quiz', 'is', 'better', 'but', 'this', 'game', 'is', 'more', 'graphic', 'and', 'a', 'little', 'more', 'sophisticated']
['work

['haven', 't', 'quite', 'finished', 'the', 'game', 'yet', 'but', 'overall', 'i', 'd', 'say', 'it', 's', 'pretty', 'good', 'and', 'definately', 'worth', 'a', 'try', 'the', 'visuals', 'and', 'sounds', 'are', 'excellent', 'and', 'for', 'the', 'most', 'part', 'the', 'ai', 'seems', 'pretty', 'smart', 'but', 'i', 'have', 'noticed', 'a', 'couple', 'small', 'problems', 'with', 'the', 'alien', 's', 'ai', 'nothing', 'serious', 'though', 'really', 'my', 'only', 'real', 'problems', 'so', 'far', 'are', 'rarely', 'and', 'i', 'mean', 'really', 'rarely', 'for', 'me', 'at', 'least', 'the', 'fps', 'drops', 'drastically', 'to', 'the', 'point', 'where', 'you', 'literally', 'just', 'cannot', 'keep', 'playing', 'without', 'restarting', 'your', 'xbox', 'for', 'most', 'games', 'that', 'wouldn', 't', 'be', 'a', 'huge', 'problem', 'however', 'this', 'game', 'has', 'manual', 'save', 'points', 'throughout', 'the', 'game', 'there', 'are', 'no', 'auto', 'saves', 'or', 'anything', 'of', 'the', 'sort', 'so', 'if', 't

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [41]:
wordCount = defaultdict(int)
for d in data['reviewText']:
    for w in re.sub(r'[^\w\s]',' ', d.lower()).split():
        #w = stemmer.stem(w)
        wordCount[w] += 1

In [42]:
most_common = sorted(wordCount.items(), key=lambda x:x[1], reverse = True)
most_common[:10]

[('the', 396835),
 ('and', 206362),
 ('i', 195415),
 ('to', 192768),
 ('a', 185475),
 ('it', 176695),
 ('is', 129281),
 ('of', 127231),
 ('you', 117996),
 ('game', 115677)]

In [43]:
words = [w[0] for w in most_common[:1000]]
wordId = dict(zip(words, range(len(words))))
wordSet = set(words)

In [49]:
def feature(datum):
    feat = [0]*len(wordSet)
    words = re.sub(r'[^\w\s]',' ', datum.lower()).split()
    for w in words:
        if not (w in wordSet): continue
        feat[wordId[w]] += 1
    #feat.append(1)
    return feat

In [50]:
X = [feature(d) for d in data['reviewText']]
y = [d for d in data['overall']]

In [51]:
clf = linear_model.Ridge(1.0, fit_intercept=True) # MSE + 1.0 l2
clf.fit(X, y)
theta = clf.coef_

In [52]:
test_data = df.sample(n = 50000)

In [53]:
test_x = [feature(d) for d in test_data['reviewText']]
test_y = [d for d in test_data['overall']]
predictions = clf.predict(test_x)

AttributeError: 'float' object has no attribute 'lower'

In [ ]:
mse = []
for rate, pred in zip(test_y, predictions):
    mse.append((rate - pred)**2)

sum(mse) / len(mse)